In [1]:
import numpy as np
import random

import torch
import torch.nn as nn
import torch.nn.functional as func
import torch.optim as optim

from matplotlib import pyplot as plt

from numpy import exp,arange
from pylab import meshgrid,cm,imshow,contour,clabel,colorbar,axis,title,show

In [2]:
# ==========
# helping methods
# ==========

# generate a list from lower and upper bound
def gen_list(p0, pn, delta, dig=5):
    ret = []
    i = p0
    while i < pn:
        ret.append(float(i))
        i += delta
        i = round(i, dig)
    return ret

# padding and zero padding
def padding(origin, a_list, b_list):
    return np.hstack((a_list, origin, b_list))

def zero_padding(origin, num):
    zero_list = [0 for i in range(num)]
    return padding(origin, zero_list, zero_list)

# trainning pairs
def gen_pair(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-1-length)
        train = current_t[p-length:p+length+1]
        solu = next_t[p]
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

# trainning pairs (in average)
def gen_pair_ave(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-2-length)
        train0 = current_t[p-length:p+length+2]
        solu1 = next_t[p]
        solu2 = next_t[p+1]
        train = []
        for j in range(len(train0)-1):
                train.append(0.5 * (train0[j] + train0[j+1]))
        solu = 0.5 * (solu1 + solu2)
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

In [3]:
# the analytical representation of exact solution
def heat_equ_analytical_solu(x, t):
    return np.sin(np.pi * x) * np.exp(-np.power(np.pi, 2) * t)

In [4]:
# restnet
class ResNet(nn.Module):
    def __init__(self, i, h, o):
        super(ResNet, self).__init__()
        self.linear1 = nn.Linear(i, h)
        self.relu1 = nn.ReLU()
        self.linear2 = nn.Linear(h, o)
        self.relu2 = nn.ReLU()
        
    def forward(self, x):
        out = self.linear1(x)
        out = self.relu1(out)
        out = self.linear2(out)
        out = self.relu2(out)
        return out + torch.mean(x)

    def load_model(self, save_path):
        self.load_state_dict(torch.load(save_path))

    def save_model(self, save_path):
        torch.save(self.state_dict(), save_path)

## $\Delta x=\frac{1}{20}$ $\Delta t=\frac{1}{80}$

In [5]:
x_1 = arange(0, 2 * np.pi, 1/20)
t_1 = arange(0, 2 * np.pi, 1/80)
X_1,T_1 = meshgrid(x_1, t_1) # grid of point
Z_1 = heat_equ_analytical_solu(X_1, T_1) # evaluation of the function on the grid

In [6]:
# preparing the trainning set
data_pairs_1 = gen_pair_ave(Z_1, len(Z_1[0]), len(Z_1), length=3, num=10000)
print(data_pairs_1)

[{'input': [-1.7344625145652128e-20, -2.843278004835861e-20, -3.8820825543287567e-20, -4.825297347440744e-20, -5.649697305614981e-20, -6.33498296585462e-20, -6.864280320871845e-20], 'solu': -4.2652564337856286e-20}, {'input': [-4.5635805125886705e-15, 4.563580512588614e-15, 1.357837103989068e-14, 2.225881700816079e-14, 3.0391177028911544e-14, 3.777520540867668e-14, 4.422908286256113e-14], 'solu': 1.967538073127641e-14}, {'input': [1.9698134398137244e-08, 3.2290851949927595e-08, 4.4088461559517125e-08, 5.4800466924296445e-08, 6.416310292107705e-08, 7.194583037881081e-08, 7.795701271809676e-08], 'solu': 4.8440132761410574e-08}, {'input': [-1.056423505982371e-12, -1.2369130036105466e-12, -1.3869455980109256e-12, -1.502826988779738e-12, -1.581703791487968e-12, -1.6216337974758396e-12, -1.6216337974758396e-12], 'solu': -1.3284036239049936e-12}, {'input': [4.576849690203354e-06, 1.3617851841543997e-05, 2.2323537285486707e-05, 3.047954315388811e-05, 3.788504151403656e-05, 4.4357684418865246e-

In [7]:
model_1 = ResNet(7, 6, 1)
optimizer_1 = optim.Adam(model_1.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_1 = nn.MSELoss()
model_1.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [8]:
list_of_loss_1 = []
list_of_output_1 = []
for data in data_pairs_1:
    output = model_1(torch.FloatTensor(data["input"]))
    loss = criterion_1(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_1.append(np.log10(loss.item()))
    list_of_output_1.append(output)
    model_1.zero_grad()
    loss.backward()
    optimizer_1.step()

<ipython-input-8-ac38450c9edb>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_1.append(np.log10(loss.item()))


In [9]:
list_of_loss_1_file = open('list_of_loss_13 xx.txt', 'w+')
for value in list_of_loss_1:
    list_of_loss_1_file.write(str(value)+" ")
list_of_loss_1_file.close()

list_of_output_1_file = open('list_of_output_13 xx.txt', 'w+')
for value in list_of_output_1:
    list_of_output_1_file.write(str(value)+" ")
list_of_output_1_file.close()

In [10]:
model_1.save_model("model_xx delta x=1 20 delta t=1 80")

## $\Delta x=\frac{1}{40}$ $\Delta t=\frac{1}{80}$

In [11]:
x_2 = arange(0, 2 * np.pi, 1/40)
t_2 = arange(0, 2 * np.pi, 1/80)
X_2,T_2 = meshgrid(x_2, t_2) # grid of point
Z_2 = heat_equ_analytical_solu(X_2, T_2) # evaluation of the function on the grid

In [12]:
# preparing the trainning set
data_pairs_2 = gen_pair_ave(Z_2, len(Z_2[0]), len(Z_2), length=3, num=10000)
print(data_pairs_2)

[{'input': [-1.1599522637923409e-26, -1.1456049160864344e-26, -1.124194533120563e-26, -1.095853117025386e-26, -1.0607554020556074e-26, -1.0191177772951906e-26, -9.711969525466988e-27], 'solu': -9.686645653776458e-27}, {'input': [-1.2022877765633119e-11, -1.3670205947975749e-11, -1.5233252764844345e-11, -1.6702381512847135e-11, -1.8068534524717765e-11, -1.9323289012846072e-11, -2.045890899856454e-11], 'solu': -1.4763844604311813e-11}, {'input': [1.0758211157953273e-18, 1.785663903163664e-18, 2.4844974787754857e-18, 3.168013301251412e-18, 3.831997268253799e-18, 4.472355697829002e-18, 5.085140567317908e-18], 'solu': 2.800322579632895e-18}, {'input': [-4.2302391861260324e-14, -3.3175424447857465e-14, -2.384391951078557e-14, -1.4365408881021852e-14, -4.798330728523436e-15, 4.798330728523317e-15, 1.4365408881021732e-14], 'solu': -1.2698109202790864e-14}, {'input': [-3.127325922003715e-11, -3.088644302256719e-11, -3.0309201633078566e-11, -2.954509393668972e-11, -2.859883091144046e-11, -2.7476

In [13]:
model_2 = ResNet(7, 6, 1)
optimizer_2 = optim.Adam(model_2.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_2 = nn.MSELoss()
model_2.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [14]:
list_of_loss_2 = []
list_of_output_2 = []
for data in data_pairs_2:
    output = model_2(torch.FloatTensor(data["input"]))
    loss = criterion_2(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_2.append(np.log10(loss.item()))
    list_of_output_2.append(output)
    model_2.zero_grad()
    loss.backward()
    optimizer_2.step()

<ipython-input-14-de329c128c88>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_2.append(np.log10(loss.item()))


In [15]:
list_of_loss_2_file = open('list_of_loss_23 xx.txt', 'w+')
for value in list_of_loss_2:
    list_of_loss_2_file.write(str(value)+" ")
list_of_loss_2_file.close()

list_of_output_2_file = open('list_of_output_23 xx.txt', 'w+')
for value in list_of_output_2:
    list_of_output_2_file.write(str(value)+" ")
list_of_output_2_file.close()

In [16]:
model_2.save_model("model_xx delta x=1 40 delta t=1 80")

## $\Delta x=\frac{1}{80}$ $\Delta t=\frac{1}{80}$

In [17]:
x_3 = arange(0, 2 * np.pi, 1/80)
t_3 = arange(0, 2 * np.pi, 1/80)
X_3,T_3 = meshgrid(x_3, t_3) # grid of point
Z_3 = heat_equ_analytical_solu(X_3, T_3) # evaluation of the function on the grid

In [18]:
# preparing the trainning set
data_pairs_3 = gen_pair_ave(Z_3, len(Z_3[0]), len(Z_3), length=3, num=10000)
print(data_pairs_3)

[{'input': [-1.1909210838582023e-21, -1.2697752068389314e-21, -1.3466714284858577e-21, -1.4214911803987545e-21, -1.4941190959432108e-21, -1.5644431881376334e-21, -1.6323550223290536e-21], 'solu': -1.2565079343723845e-21}, {'input': [1.1596216882960277e-17, 1.1213650012634218e-17, 1.0813792506770246e-17, 1.0397260916660138e-17, 9.964697503825037e-18, 9.51676924969474e-18, 9.05416682717061e-18], 'solu': 9.190518392001978e-18}, {'input': [-1.079288153569185e-23, -1.1191965824505905e-23, -1.1573792913228457e-23, -1.1937774052164036e-23, -1.2283348008778286e-23, -1.2609981933077839e-23, -1.2917172179226308e-23], 'solu': -1.055223417642382e-23}, {'input': [-2.6157320370213172e-20, -3.0817643466497805e-20, -3.5430447990264484e-20, -3.9988621331280246e-20, -4.448513511663624e-20, -4.891305604798929e-20, -5.326555659220542e-20], 'solu': -3.534740185533323e-20}, {'input': [1.3536703684987169e-08, 1.3268496356787739e-08, 1.2979829968925943e-08, 1.2671149624048908e-08, 1.2342931284874833e-08, 1.19

In [19]:
model_3 = ResNet(7, 6, 1)
optimizer_3 = optim.Adam(model_3.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_3 = nn.MSELoss()
model_3.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [20]:
list_of_loss_3 = []
list_of_output_3 = []
for data in data_pairs_3:
    output = model_3(torch.FloatTensor(data["input"]))
    loss = criterion_3(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_3.append(np.log10(loss.item()))
    list_of_output_3.append(output)
    model_3.zero_grad()
    loss.backward()
    optimizer_3.step()

<ipython-input-20-3f959fb14d49>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_3.append(np.log10(loss.item()))


In [21]:
list_of_loss_3_file = open('list_of_loss_33 xx.txt', 'w+')
for value in list_of_loss_3:
    list_of_loss_3_file.write(str(value)+" ")
list_of_loss_3_file.close()

list_of_output_3_file = open('list_of_output_33 xx.txt', 'w+')
for value in list_of_output_3:
    list_of_output_3_file.write(str(value)+" ")
list_of_output_3_file.close()

In [22]:
model_3.save_model("model_xx delta x=1 80 delta t=1 80")

## $\Delta x=\frac{1}{160}$ $\Delta t=\frac{1}{80}$

In [23]:
x_4 = arange(0, 2 * np.pi, 1/160)
t_4 = arange(0, 2 * np.pi, 1/80)
X_4,T_4 = meshgrid(x_4, t_4) # grid of point
Z_4 = heat_equ_analytical_solu(X_4, T_4) # evaluation of the function on the grid

In [24]:
# preparing the trainning set
data_pairs_4 = gen_pair_ave(Z_4, len(Z_4[0]), len(Z_4), length=3, num=10000)
print(data_pairs_4)

[{'input': [-1.9721355683533398e-23, -1.8484815832705895e-23, -1.7241149733500213e-23, -1.5990836842872038e-23, -1.4734359180241435e-23, -1.34722011416655e-23, -1.220484931309444e-23], 'solu': -1.413488430134808e-23}, {'input': [0.001717158540207775, 0.0017304061865605121, 0.001742986728388542, 0.0017548953156535086, 0.0017661273573683313, 0.0017766785233671169, 0.0017865447459745228], 'solu': 0.001551216017740616}, {'input': [-3.646769045948205e-25, -3.634004137514472e-25, -3.619838251309296e-25, -3.6042768485514693e-25, -3.5873259284579775e-25, -3.5689920259311943e-25, -3.5492822090395468e-25], 'solu': -3.1859518513573905e-25}, {'input': [3.945852800406892e-06, 4.230481345264691e-06, 4.513478959032996e-06, 4.7947365407445945e-06, 5.074145660247753e-06, 5.351598600008107e-06, 5.6269883966358205e-06], 'solu': 4.238242621372272e-06}, {'input': [1.879018643772318e-25, 1.8918566402569786e-25, 1.9039652899936824e-25, 1.9153399248674572e-25, 1.9259761597400332e-25, 1.9358698941403976e-25, 1

In [25]:
model_4 = ResNet(7, 6, 1)
optimizer_4 = optim.Adam(model_4.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_4 = nn.MSELoss()
model_4.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [26]:
list_of_loss_4 = []
list_of_output_4 = []
for data in data_pairs_4:
    output = model_4(torch.FloatTensor(data["input"]))
    loss = criterion_4(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_4.append(np.log10(loss.item()))
    list_of_output_4.append(output)
    model_4.zero_grad()
    loss.backward()
    optimizer_4.step()

<ipython-input-26-f52da78e2a74>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_4.append(np.log10(loss.item()))


In [27]:
list_of_loss_4_file = open('list_of_loss_43 xx.txt', 'w+')
for value in list_of_loss_4:
    list_of_loss_4_file.write(str(value)+" ")
list_of_loss_4_file.close()

list_of_output_4_file = open('list_of_output_43 xx.txt', 'w+')
for value in list_of_output_4:
    list_of_output_4_file.write(str(value)+" ")
list_of_output_4_file.close()

In [28]:
model_4.save_model("model_xx delta x=1 160 delta t=1 80")